# Model Pipeline

By: Aditya Mengani, Ognjen Sosa, Sanjay Elangovan, Song Park, Sophia Skowronski

**Can we improve on the baseline scores using different encoding, imputing, and scaling schemes?**
- Averaged Logistic Regression accuracy Score: 0.5
- Averaged Linear Regression accuracy score: 0.2045
- Averaged K-Nearest Neighbour accuracy score: 0.6198
- Averaged Naive Bayes accuracy score: 0.649

**`p1_tag` ~  `rank` + `total_funding_usd` + `employee_count` (ordinal) + `country` (nominal) + `category_groups` (nominal)**

### STEPS FOR CONNECTING TO COLAB

https://www.marktechpost.com/2019/06/07/how-to-connect-google-colab-with-google-drive/

*  Upload the .csv files to your google drive
*  Go to the file in google drive, right click on file name, then click on 'Get Link' and it shows the unique id of the file. Copy it and save it in the below code:
downloaded = drive.CreateFile({'id':"1uWwO-geA8IRNaerjQCk92******"}) 
*  Replace the id with id of file you want to access
downloaded.GetContentFile('baseline.csv')


### Enabling GPU settings in COLAB

https://www.tutorialspoint.com/google_colab/google_colab_using_free_gpu.htm

In [ ]:
## GCP drive to colab connectivity Code

from google.colab import drive
drive.mount('/content/drive')

from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from google.colab import auth
from oauth2client.client import GoogleCredentials

auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)

downloaded = drive.CreateFile({'id':"1uWwO-geA8IRNaerjQCk92KCWDlZM_6Zx"})   # replace the id with id of file you want to access
downloaded.GetContentFile('baseline.csv')

downloaded = drive.CreateFile({'id':"13zLq9t_noAl7RRsLuWmbI_fRe3rE0dpg"})   # replace the id with id of file you want to access
downloaded.GetContentFile('pagerank_df_deg3.csv')


In [ ]:
#pip install prince

In [ ]:
#pip install category_encoders

In [ ]:
#pip install from libsvm

## Reading in data

 * Read data
 * Create age feature
 * Impute the na and infinite values
 * One-hot encode countrycode

In [1]:
print("***************Model Set up Options************************ ")
print("Option 1 : Graph + Baseline")
print("Option 2 : Baseline only")
print("Option 3 : Graph + Baseline reduced")
print("Option 4 : Baseline reduced only")
print("Option 5 : Graph only")
print("*********************************************************** ")


***************Model Set up Options************************ 
Option 1 : Graph + Baseline
Option 2 : Baseline only
Option 3 : Graph + Baseline reduced
Option 4 : Baseline reduced only
Option 5 : Graph only
*********************************************************** 


### BASELINE ONLY METHOD

In [2]:
def Baseline_Only():
    df = pd.read_csv('files/output/baseline.csv',sep=';')
    df = df[df.columns.to_list()[61:]]
    print("Original DF shape",df.shape)

    # create column map
    column_map = {'employee_count':'employee_count_ord', 'employee_size':'employee_count', 'category_groups':'category_groups_list', 'country':'country_code'}
    df = df.rename(column_map, axis=1)

    #print('\nStarting Dataframe Columns:\n\n{}\n'.format(df.columns.to_list()))

    # Have industry mapper for 'ind_1'...'ind_46' columns
    industries = ['Software', 'Information Technology', 'Internet Services', 'Data and Analytics',
                  'Sales and Marketing', 'Media and Entertainment', 'Commerce and Shopping', 
                  'Financial Services', 'Apps', 'Mobile', 'Science and Engineering', 'Hardware',
                  'Health Care', 'Education', 'Artificial Intelligence', 'Professional Services', 
                  'Design', 'Community and Lifestyle', 'Real Estate', 'Advertising',
                  'Transportation', 'Consumer Electronics', 'Lending and Investments',
                  'Sports', 'Travel and Tourism', 'Food and Beverage',
                  'Content and Publishing', 'Consumer Goods', 'Privacy and Security',
                  'Video', 'Payments', 'Sustainability', 'Events', 'Manufacturing',
                  'Clothing and Apparel', 'Administrative Services', 'Music and Audio',
                  'Messaging and Telecommunications', 'Energy', 'Platforms', 'Gaming',
                  'Government and Military', 'Biotechnology', 'Navigation and Mapping',
                  'Agriculture and Farming', 'Natural Resources']
    industry_map = {industry:'ind_'+str(idx+1) for idx,industry in enumerate(industries)}

    # Imputing data(TBD)
    # Rank has na() values, imputing to zero for now
    # total_funding_usd has na() values, imputing to zero for now
    # Age has infinite values, imputing to zero for now
    df['rank'] = df['rank'].fillna(0)
    df['total_funding_usd'] = df['total_funding_usd'].fillna(0)
    df['founded_on'] = df['founded_on'].fillna(0)
    df = df.fillna(0)

    # create age feature
    print("DF shape before adding age",df.shape)
    today = datetime.strptime('09-08-2020', '%m-%d-%Y')
    df['founded_on2'] = pd.to_datetime(df['founded_on'].fillna(0))
    diff_y = today.year - df['founded_on2'].dt.year
    founded_md = df['founded_on2'].apply(lambda x: (x.month,x.day) )
    no_years = founded_md > (today.month,today.day)
    df['age'] = diff_y - no_years

    print("DF shape after adding age",df.shape)

    # Encode country_code using one-hotencoding
    df = pd.concat([df,pd.get_dummies(df['country_code'], prefix='country')],axis=1)
    df_simple = df.drop(['employee_count','category_groups_list',#'uuid',
                         'founded_on','founded_on2','country_code'], axis=1)
    df_simple = reduce_mem_usage(df_simple)

    print('\nEnding Dataframe Columns:\n\n{}'.format(df_simple.columns.to_list()))
    print('\nDataframe shape:', df_simple.shape)

    del industries, industry_map
    
    return df_simple

### BASELINE REDUCED METHOD

In [3]:
# ELIMINIATING FEATURES: RANK and total_funding_usd (For now)
def Baseline_Reduced():
    df = pd.read_csv('files/output/baseline.csv',sep=';')
    df = df[df.columns.to_list()[61:]]
    print("Original DF shape",df.shape)

    # create column map
    column_map = {'employee_count':'employee_count_ord', 'employee_size':'employee_count', 'category_groups':'category_groups_list', 'country':'country_code'}
    df = df.rename(column_map, axis=1)

    #print('\nStarting Dataframe Columns:\n\n{}\n'.format(df.columns.to_list()))

    # Have industry mapper for 'ind_1'...'ind_46' columns
    industries = ['Software', 'Information Technology', 'Internet Services', 'Data and Analytics',
                  'Sales and Marketing', 'Media and Entertainment', 'Commerce and Shopping', 
                  'Financial Services', 'Apps', 'Mobile', 'Science and Engineering', 'Hardware',
                  'Health Care', 'Education', 'Artificial Intelligence', 'Professional Services', 
                  'Design', 'Community and Lifestyle', 'Real Estate', 'Advertising',
                  'Transportation', 'Consumer Electronics', 'Lending and Investments',
                  'Sports', 'Travel and Tourism', 'Food and Beverage',
                  'Content and Publishing', 'Consumer Goods', 'Privacy and Security',
                  'Video', 'Payments', 'Sustainability', 'Events', 'Manufacturing',
                  'Clothing and Apparel', 'Administrative Services', 'Music and Audio',
                  'Messaging and Telecommunications', 'Energy', 'Platforms', 'Gaming',
                  'Government and Military', 'Biotechnology', 'Navigation and Mapping',
                  'Agriculture and Farming', 'Natural Resources']
    industry_map = {industry:'ind_'+str(idx+1) for idx,industry in enumerate(industries)}

    # Imputing data(TBD)
    # Rank has na() values, imputing to zero for now
    # total_funding_usd has na() values, imputing to zero for now
    # Age has infinite values, imputing to zero for now
    df['rank'] = df['rank'].fillna(0)
    df['total_funding_usd'] = df['total_funding_usd'].fillna(0)
    df['founded_on'] = df['founded_on'].fillna(0)
    df = df.fillna(0)

    # create age feature
    print("DF shape before adding age",df.shape)
    today = datetime.strptime('09-08-2020', '%m-%d-%Y')
    df['founded_on2'] = pd.to_datetime(df['founded_on'].fillna(0))
    diff_y = today.year - df['founded_on2'].dt.year
    founded_md = df['founded_on2'].apply(lambda x: (x.month,x.day) )
    no_years = founded_md > (today.month,today.day)
    df['age'] = diff_y - no_years

    print("DF shape after adding age",df.shape)

    # Encode country_code using one-hotencoding
    df = pd.concat([df,pd.get_dummies(df['country_code'], prefix='country')],axis=1)
    df_simple = df.drop(['employee_count','category_groups_list',#'uuid',
                         'founded_on','founded_on2','country_code','rank','total_funding_usd'], axis=1)
    df_simple = reduce_mem_usage(df_simple)

    #print('\nEnding Dataframe Columns:\n\n{}'.format(df_simple.columns.to_list()))
    print('\nDataframe shape:', df_simple.shape)

    del industries, industry_map
    
    return df_simple

### GRAPH ONLY METHOD

In [4]:
def Graph_Only(n_degrees):
    df = pd.read_csv('files/output/baseline.csv',sep=';')
    df = df[['uuid','p1_tag']]
    df['__id'] = df['uuid']
    print("Original DF shape",df.shape)
    
    if n_degrees == 2:
        df_gr = pd.read_csv('files/output/Model_DF_D2.csv',sep=',')
        print("Original Model_DF_D2 shape",df.shape)
        #print(df_gr.columns)
    elif n_degrees == 4:
        df_gr = pd.read_csv('files/output/Model_DF_D4.csv',sep=',')
        print("Original Model_DF_D4 shape",df.shape)
        #print(df_gr.columns)
    elif n_degrees == 0:
        df_gr = pd.read_csv('files/output/Model_DF_ALLLLL.csv',sep=',')
        print("Original Model_DF_ALLLLL.csv shape",df.shape)
        
    df_gr = pd.merge(df_gr.copy(),df.copy(), how = 'left',on='__id')
    print("Original DF_GR shape after merge",df_gr.shape)
    #print(df_gr.columns)
    df_gr = reduce_mem_usage(df_gr) 
    df_gr = df_gr.fillna(0)
    del df

    #impute
    return df_gr

### GENERATE TRAIN TEST SPLIT

In [5]:
## Select equal sample of non-Pledge 1% organizations
def gen_Train_Test_Split(df_simple):
    df_p1 = df_simple[df_simple['p1_tag']==1]
    print(df_p1.shape)
    df_notp1 = df_simple[df_simple['p1_tag']==0].sample(n=df_p1.shape[0], replace=True)
    df_model = pd.concat([df_p1, df_notp1]).reset_index(drop=True)
    df_model = reduce_mem_usage(df_model)

    # Create variable for each feature type: categorical and numerical
    numeric_features = df_model.select_dtypes(include=['uint8','int8', 'int16', 'int32', 'int64', 'float16', 'float32','float64']).drop(['p1_tag'], axis=1).columns
    categorical_features = df_model.select_dtypes(include=['object']).columns
    print('Numeric features:', numeric_features.to_list())
    print('Categorical features:', categorical_features.to_list())

    X = df_model.drop('p1_tag', axis=1)
    y = df_model['p1_tag']
    y = preprocessing.LabelEncoder().fit_transform(y)

    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2,random_state=99)
    print('Training data shape:', X_train.shape)
    print('Train label shape:', y_train.shape)
    print('Test data shape:',  X_test.shape)
    print('Test label shape:', y_test.shape)

    # reset indexes for train and test
    X_train= X_train.reset_index(drop=True)
    X_test= X_test.reset_index(drop=True)
    return X_train,X_test,X,y,y_train,y_test,numeric_features,categorical_features

### PERFORM PCA COUNTRY

In [6]:
# Perform PCA of country dataset
def PCA_Country(X_train,X_test):
    # Perform PCA of country dataset
    country_train = X_train.filter(regex='^country',axis=1).fillna(0)
    country_test = X_test.filter(regex='^country',axis=1).fillna(0)
#     # For each value of k, use PCA to project the data feature sets to k principle components
#     matrix = [['k', 'total variance']] # For display
#     k_values = list(range(1,113)) # To loop through, there are 112 country codes
#     # For each value of k, use PCA to project the data feature sets to k principle components
#     for k in k_values:
#         pca = PCA(n_components=k, whiten=True,random_state=random.seed(1234))
#         pca.fit(country_train)
#         matrix.append([k, round(pca.explained_variance_ratio_.sum(),4)])
#     # Print results
#     print('Fraction of the total variance in the training data explained by the first k principal components:\n')
#     s = [[str(e) for e in row] for row in matrix]
#     lens = [max(map(len, col)) for col in zip(*s)]
#     fmt = '\t'.join('{{:{}}}'.format(x) for x in lens)
#     table = [fmt.format(*row) for row in s]
#     print('\n'.join(table))
#     print()
#     # Plots
#     _, ax = plt.subplots(nrows=1, ncols=1, figsize=(8,5))
#     # Plotting lineplot of fraction of total variance vs. number of principal components
#     # For all possible numbers of principal components
#     ax.plot(np.cumsum(PCA().fit(country_train).explained_variance_ratio_))
#     # Labels
#     ax.set_title('Fraction of total variance vs. number of principal components')
#     ax.set_xlabel('k = number of components')
#     ax.set_ylabel('Cumulative explained variance')
#     # Display
#     plt.show()
    
    # create PCA features for train and test set
    n_components = 15
    pca = PCA(n_components=n_components,whiten=True,random_state=random.seed(1234))  
    pca_train = pca.fit_transform(country_train)
    pca_test = pca.transform(country_test)
    # create dataframes from numpy
    df_cty_train = pd.DataFrame(pca_train,columns=['cntry_pca_'+ str(x) for x in range(n_components)])
    df_cty_test = pd.DataFrame(pca_test,columns=['cntry_pca_'+ str(x) for x in range(n_components)])
    # drop country prefix columns
    X_train = X_train.drop(list(X_train.filter(regex='^country_',axis=1).columns), axis=1)
    X_test = X_test.drop(list(X_test.filter(regex='^country_',axis=1).columns), axis=1)
    # concat with train dataset
    X_train = pd.concat([X_train, df_cty_train],axis = 1)
    X_test = pd.concat([X_test, df_cty_test],axis = 1)
    del df_cty_train,df_cty_test,country_train,country_test
    return X_train,X_test


### PERFORM PCA INDUSTRY

In [7]:
# Perform PCA of country dataset
def PCA_Industry(X_train,X_test):
    # Perform PCA of industry dataset
    industry_train = X_train.filter(regex='^ind_',axis=1).fillna(0)
    industry_test = X_test.filter(regex='^ind_',axis=1).fillna(0)
#     # For each value of k, use PCA to project the data feature sets to k principle components
#     matrix = [['k', 'total variance']] # For display
#     k_values = list(range(1,47)) # To loop through, there are 46 industries
#     # For each value of k, use PCA to project the data feature sets to k principle components
#     for k in k_values:
#         pca = PCA(n_components=k, whiten=True,random_state=random.seed(1234))
#         pca.fit(industry_train)
#         matrix.append([k, round(pca.explained_variance_ratio_.sum(),4)])
#     # Print results
#     print('Fraction of the total variance in the training data explained by the first k principal components:\n')
#     s = [[str(e) for e in row] for row in matrix]
#     lens = [max(map(len, col)) for col in zip(*s)]
#     fmt = '\t'.join('{{:{}}}'.format(x) for x in lens)
#     table = [fmt.format(*row) for row in s]
#     print('\n'.join(table))
#     print()
#     # Plots
#     _, ax = plt.subplots(nrows=1, ncols=1, figsize=(8,5))
#     # Plotting lineplot of fraction of total variance vs. number of principal components
#     # For all possible numbers of principal components
#     ax.plot(np.cumsum(PCA().fit(industry_train).explained_variance_ratio_))
#     # Labels
#     ax.set_title('Fraction of total variance vs. number of principal components')
#     ax.set_xlabel('k = number of components')
#     ax.set_ylabel('Cumulative explained variance')
#     # Display
#     plt.show()
    
    # create PCA features for train and test set
    n_components=10
    pca = PCA(n_components=n_components, whiten=True, random_state=random.seed(1234)) 
    pca_train = pca.fit_transform(industry_train)
    pca_test = pca.transform(industry_test)
    # create dataframes from numpy
    df_ind_train = pd.DataFrame(pca_train,columns=['ind_pca'+ str(x) for x in range(n_components)])
    df_ind_test = pd.DataFrame(pca_test,columns=['ind_pca'+ str(x) for x in range(n_components)])
    # drop country prefix columns
    X_train = X_train.drop(list(X_train.filter(regex='^ind_',axis=1).columns), axis=1)
    X_test = X_test.drop(list(X_test.filter(regex='^ind_',axis=1).columns), axis=1)
    # concat with train dataset
    X_train = pd.concat([X_train, df_ind_train],axis = 1)
    X_test = pd.concat([X_test, df_ind_test],axis = 1)
    del df_ind_train,df_ind_test,industry_train,industry_test

    return X_train,X_test


### VIZUALIZE COUNTRY INDUSTRY PCA

In [8]:
# create graphs for PCA analysis for country and industry features
def Visualize_Country_Ind_PCA(X,y):
    print("None")
#     Country_df = X.filter(regex='^country',axis=1).fillna(0)
#     pca_new_Country = PCA(n_components=10,random_state=random.seed(1234))  
#     Country_df_PCA = pca_new_Country.fit_transform(Country_df)

#     Industry_df = X.filter(regex='^ind_',axis=1).fillna(0)
#     pca_new_Industry_df = PCA(n_components=30,random_state=random.seed(1234))  
#     Industry_df_PCA = pca_new_Industry_df.fit_transform(Industry_df)

#     # The PCA model
#     fig, axes = plt.subplots(1,2,figsize=(15,15))
#     colors = ['r','g']
#     fig.suptitle('PCA Analysis for Country and Industry', fontsize=30)
#     targets = [1,0]
#     for target, color in zip(targets,colors):
#       indexes = np.where(y == target)
#       axes[0].scatter(Country_df_PCA[indexes][:,0], Country_df_PCA[indexes][:,1],color=color)
#       axes[0].set_xlabel('PC1')
#       axes[0].set_ylabel('PC2')
#       axes[0].set_title('PCA-Country')
#       axes[1].scatter(Industry_df_PCA[indexes][:,0], Industry_df_PCA[indexes][:,1], color=color)
#       axes[1].set_xlabel('PC1')
#       axes[1].set_ylabel('PC2')
#       axes[1].set_title('PCA-Industry')
#     plt.axis('tight')

#     out_labels = ['p1','non-p1']
#     plt.legend(out_labels,prop={'size':10},loc='upper right',title='Legend of plot')

#     plt.show()

### RUN CLASSIFIER

In [12]:
def Run_Classifier(X_train,X_test,y_train,y_test,numeric_features,categorical_features,Type,col_graph):
    
    results = OrderedDict()
    results['Model_Type'] = Type
    results['Column_Name'] = col_graph
    classifier_list = []
    LRR = LogisticRegression(max_iter=10000, tol=0.1)
    KNN = KNeighborsClassifier(n_neighbors=5)
    BNB = BernoulliNB()
    GNB = GaussianNB()
    SVM = svm.SVC()
    DCT = DecisionTreeClassifier()
    XGB = xgb.XGBRegressor() #tree_method='gpu_hist', gpu_id=0
    RMF = RandomForestClassifier()

    #classifier
    classifier_list.append(('LRR', LRR, {'classifier__C': [0.0001, 0.001, 0.01, 0.1, 1.0, 10.0, 100.0, 1000],\
                                        'classifier__random_state': [random.seed(1234)]}))
    classifier_list.append(('KNN', KNN, {}))
    classifier_list.append(('BNB', BNB, {'classifier__alpha': [0.0001, 0.001, 0.01, 0.1, 1.0, 10.0]}))
    classifier_list.append(('GNB', GNB, {'classifier__var_smoothing': [0.0001, 0.001, 0.01, 0.1, 1.0, 10.0]}))
    classifier_list.append(('DCT', DCT, {'classifier__max_depth':np.arange(1, 21),
                                        'classifier__min_samples_leaf':[1, 5, 10, 20, 50, 100],
                                        'classifier__random_state' : [random.seed(1234)]}))
    classifier_list.append(('XGB', XGB, {'classifier__random_state' : [random.seed(1234)]}))
    classifier_list.append(('RMF', RMF, {'classifier__random_state' : [random.seed(1234)]}))
    classifier_list.append(('SVM', SVM, {'classifier__random_state' : [random.seed(1234)]}))

    encoder_list = [ce.one_hot.OneHotEncoder]
    scaler_list = [StandardScaler()]

    for label, classifier, params in classifier_list:
        results[label] = {}
        for encoder in encoder_list:
            for feature_scaler in scaler_list:
                results[label][f'{encoder.__name__} with {feature_scaler}'] = {}
                print('{} with {} and {}'.format(label,encoder.__name__,feature_scaler))

                numeric_transformer = Pipeline(steps=[('imputer', SimpleImputer(strategy='median')),('scaler', StandardScaler())])

                categorical_transformer = Pipeline(steps=[('imputer', SimpleImputer(strategy='constant', fill_value='missing')),
                                                          ('woe', encoder())])

                preprocessor = ColumnTransformer(transformers=[('num', numeric_transformer, numeric_features),
                                                               ('cat', categorical_transformer, categorical_features)])

                pipe = Pipeline(steps=[#('preprocessor', preprocessor),
                                       ('scaler', feature_scaler),
                                       ('classifier', classifier)])

                if params != {}:
                    search = RandomizedSearchCV(pipe, params, n_jobs=-1)
                    search.fit(X_train, y_train)
                    print('Best parameter (CV score={:.3f}): {}'.format(search.best_score_, search.best_params_))
                    model = search.fit(X_train, y_train)
                    y_pred = model.predict(X_test)
                    if label == 'XGB':
                        y_pred = [round(value) for value in y_pred]
                    score = f1_score(y_test, y_pred,average='weighted')
                    print('Best score: {:.4f}\n'.format(score))
                    results[label][f'{encoder.__name__} with {feature_scaler}']['score'] = score
                    try:
                        results[label][f'{encoder.__name__} with {feature_scaler}']['best_params'] = search.best_params_
                    except:
                        print('Something went wrong w/ GridSearch or pipeline fitting.')
                else:
                    try:
                        model = pipe.fit(X_train, y_train)
                        y_pred = model.predict(X_test)
                        if label == 'XGB':
                            y_pred = [round(value) for value in y_pred]
                        score = f1_score(y_test, y_pred,average='weighted')
                        print('Score: {:.4f}\n'.format(score))
                        results[label][f'{encoder.__name__} with {feature_scaler}']['score'] = score
                    except:
                        print('Something went wrong with pipeline fitting')
    print(results)
    return results    

### WRITE OUTPUT

In [13]:
def Write_Output(out_list):
    # encode to encode int/float and array types and write the output json
    class NpEncoder(json.JSONEncoder):
        def default(self, obj):
            if isinstance(obj, np.integer):
                return int(obj)
            elif isinstance(obj, np.floating):
                return float(obj)
            elif isinstance(obj, np.ndarray):
                return obj.tolist()
            else:
                return super(NpEncoder, self).default(obj)

    # File is saved under Files directory. /content would be the baseline folder
    # You can click on folder icon on left side of the directory structure to
    # see the created file
    
    with open(f'files/output/results_baseline.json', 'a+') as fp:
        json.dump(out_list, fp, sort_keys=False, indent=4, cls=NpEncoder)

### REDUCE MEMORY USAGE

In [14]:
def reduce_mem_usage(df, verbose=True):
    numerics = ['int16', 'int32', 'int64', 'float16', 'float32', 'float64']
    start_mem = df.memory_usage().sum() / 1024**2    
    for col in df.columns:
        col_type = df[col].dtypes
        if col_type in numerics:
            c_min = df[col].min()
            c_max = df[col].max()
            if str(col_type)[:3] == 'int':
                if c_min > np.iinfo(np.int8).min and c_max < np.iinfo(np.int8).max:
                    df[col] = df[col].astype(np.int8)
                elif c_min > np.iinfo(np.int16).min and c_max < np.iinfo(np.int16).max:
                    df[col] = df[col].astype(np.int16)
                elif c_min > np.iinfo(np.int32).min and c_max < np.iinfo(np.int32).max:
                    df[col] = df[col].astype(np.int32)
                elif c_min > np.iinfo(np.int64).min and c_max < np.iinfo(np.int64).max:
                    df[col] = df[col].astype(np.int64)  
            else:
                if c_min > np.finfo(np.float16).min and c_max < np.finfo(np.float16).max:
                    df[col] = df[col].astype(np.float16)
                elif c_min > np.finfo(np.float32).min and c_max < np.finfo(np.float32).max:
                    df[col] = df[col].astype(np.float32)
                else:
                    df[col] = df[col].astype(np.float64)    
    end_mem = df.memory_usage().sum() / 1024**2
    if verbose: print('Mem. usage decreased to {:5.2f} Mb ({:.1f}% reduction)'.format(end_mem, 100*(start_mem-end_mem)/start_mem))
    return df

### MAIN MODULE

In [17]:
'''Data analysis'''
import numpy as np
import pandas as pd
import csv
import warnings
import json
import os
import time
import math
import random
import itertools
import statistics
from collections import OrderedDict 
from datetime import datetime
warnings.filterwarnings('ignore')

'''Plotting'''
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

'''Stat'''
import statsmodels.api as sm
from scipy.stats import chi2_contingency

'''ML'''
import prince
import category_encoders as ce
from sklearn import metrics, svm, preprocessing, utils
from sklearn.metrics import mean_squared_error, r2_score, f1_score
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.impute import SimpleImputer
from sklearn.compose import ColumnTransformer
from sklearn.model_selection import train_test_split, GridSearchCV,RandomizedSearchCV

from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LinearRegression
from sklearn.linear_model  import LogisticRegression
from sklearn import linear_model
from sklearn.naive_bayes import GaussianNB, BernoulliNB, MultinomialNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.decomposition import PCA

from sklearn import metrics, svm
from sklearn.tree import DecisionTreeClassifier,export_graphviz
import xgboost as xgb
from sklearn.preprocessing import MinMaxScaler,StandardScaler,\
MaxAbsScaler,RobustScaler,QuantileTransformer,PowerTransformer
from libsvm.svmutil import *

#list_Set_Up = ['BL_Only','G_Only','G+BL','G+BL_Red','BL_Red_Only']
list_Set_Up = ['G_Only','G+BL']
#degrees = [2,4,0]
degrees = [2,4,0]

# Defining main function 
def main():
    final_out = []
    # Testing for 3 iterations for now
    for iteration in range(10):
        out_dict = {}
        out_list = []
        out_dict['iteration'] = iteration+1
        for n_deg,setup_Type in zip(degrees,list_Set_Up):
            print(f"\nDEGREE:{n_deg}:ITERATION:{iteration+1} BEGIN...")
            #print("n_deg",n_deg)
            if setup_Type == 'BL_Only':
                print(f"\nDEGREE:{n_deg}:BASELINE_ONLY SET UP:START...")
                df_bo = Baseline_Only()
                df_bo = df_bo.drop(['uuid'],axis=1)
                df_simple = df_bo
                X_train,X_test,X,y,y_train,y_test,numeric_features,\
                categorical_features = gen_Train_Test_Split(df_simple)
                X_train,X_test = PCA_Industry(X_train,X_test)
                X_train,X_test = PCA_Country(X_train,X_test)
                
                #Visualize_Country_Ind_PCA(X,y)
                print("Final train dataset shape",X_train.shape)
                print("\nFinal test dataset shape",X_test.shape)
                #print('\nTrain Dataframe Columns:\n\n{}'.format(X_train.columns.to_list()))
                #print('\nTest Dataframe Columns:\n\n{}'.format(X_test.columns.to_list()))
                col_graph = 'None'
                results = Run_Classifier(X_train,X_test,y_train,y_test,numeric_features,categorical_features,setup_Type,col_graph)
                out_list.append(results)
                print(f"\nDEGREE:{n_deg}:BASELINE_ONLY SET UP:END")
            elif setup_Type == 'G_Only':
                print(f"\nDEGREE:{n_deg}:BASELINE_ONLY SET UP:START...")
                df_gr = Graph_Only(n_deg)
                df_gr = df_gr.drop(['uuid','__id'],axis=1)
                df_simple = df_gr
                X_train,X_test,X,y,y_train,y_test,numeric_features,\
                categorical_features = gen_Train_Test_Split(df_simple)
                print("Final train dataset shape",X_train.shape)
                print("\nFinal test dataset shape",X_test.shape)
                #print('\nTrain Dataframe Columns:\n\n{}'.format(X_train.columns.to_list()))
                #print('\nTest Dataframe Columns:\n\n{}'.format(X_test.columns.to_list()))
                col_graph = 'None'
                results = Run_Classifier(X_train,X_test,y_train,y_test,numeric_features,categorical_features,setup_Type,col_graph)
                out_list.append(results)
                print(f"\nDEGREE:{n_deg}:BASELINE_ONLY SET UP:END")
            elif setup_Type == 'G+BL':   
                print(f"\nDEGREE:{n_deg}:GRAPH+BASELINE:START...") 
                
                df_gr = Graph_Only(n_deg)
                print("Graph shape after merge",df_gr.shape)
                
                graph_col_list = list(set(df_gr.columns) - {'__id'} - {'p1_tag'}) 
                print(graph_col_list)
                for col_graph in graph_col_list:
                    col_name = ['__id','p1_tag']
                    col_name.append(col_graph)
                    df_temp = df_gr[[c for c in col_name if (c in df_gr)]]
                    print("Get these columns: ",df_temp.columns)
                    df_temp['uuid'] = df_temp['__id']
                    df_bo = Baseline_Only()
                    df_simple = pd.merge(df_temp.copy(),df_bo.copy(), how = 'inner',on='uuid')
                    df_simple = df_simple.drop(['uuid','__id','p1_tag_y'],axis=1)
                    print("Merged shape after baseline and graph",df_simple.shape)
                    df_simple = df_simple.rename(columns={"p1_tag_x": "p1_tag"})
                    
                    print("df_bo shape",df_bo.shape)
                    print("df_temp shape",df_temp.shape)
                    print("df_simple shape",df_simple.shape)
                    
                    X_train,X_test,X,y,y_train,y_test,numeric_features,\
                    categorical_features = gen_Train_Test_Split(df_simple)
                    print("Before pca dataset shape",X_train.shape)
                    print("\nBefore pca dataset shape",X_test.shape)

                    X_train,X_test = PCA_Industry(X_train,X_test)
                    X_train,X_test = PCA_Country(X_train,X_test)
                    #Visualize_Country_Ind_PCA(X)
                    
                    print("Train set columns list",X_train.columns)
                    
                    print("Final train dataset shape",X_train.shape)
                    print("\nFinal test dataset shape",X_test.shape)
                    #print('\nTrain Dataframe Columns:\n\n{}'.format(X_train.columns.to_list()))
                    #print('\nTest Dataframe Columns:\n\n{}'.format(X_test.columns.to_list()))
                    
                    results = Run_Classifier(X_train,X_test,y_train,y_test,numeric_features,categorical_features,setup_Type,col_graph)
                    out_list.append(results)
                    print(f"\nDEGREE:{n_deg}:GRAPH+BASELINE SET UP:END")
                                        
            elif setup_Type == 'G+BL_Red':
                print(f"\nDEGREE:{n_deg}:GRAPH+BASELINE_REDUCED:START...") 
                df_gr = Graph_Only(n_deg)
                print("Graph shape after merge",df_gr.shape)
                
                df_bo = Baseline_Reduced()
                df_temp = df_bo
                df_temp = df_temp.drop(['uuid'],axis=1)
                        
                df_simple = pd.merge(df_gr.copy(),df_bo.copy(), how = 'outer',on='uuid')
                df_simple = df_simple.drop(['uuid','__id','p1_tag_y'],axis=1)
                print("Merged shape after baseline and graph",df_simple.shape)
                #print(list(df_simple.columns))
                df_simple = df_simple.rename(columns={"p1_tag_x": "p1_tag"})
                               
                X_train,X_test,X,y,y_train,y_test,numeric_features,\
                categorical_features = gen_Train_Test_Split(df_simple)
                print("Before pca dataset shape",X_train.shape)
                print("\nBefore pca dataset shape",X_test.shape)
                
                X_train,X_test = PCA_Industry(X_train,X_test)
                X_train,X_test = PCA_Country(X_train,X_test)
                #Visualize_Country_Ind_PCA(X)
                
                print("Final train dataset shape",X_train.shape)
                print("\nFinal test dataset shape",X_test.shape)
                #print('\nTrain Dataframe Columns:\n\n{}'.format(X_train.columns.to_list()))
                #print('\nTest Dataframe Columns:\n\n{}'.format(X_test.columns.to_list()))
                col_graph = 'None'
                results = Run_Classifier(X_train,X_test,y_train,y_test,numeric_features,categorical_features,setup_Type,col_graph)
                out_list.append(results)
                print(f"\nDEGREE:{n_deg}:GRAPH+BASELINE_REDUCED SET UP:END")               
            elif setup_Type == 'BL_Red_Only':
                print(f"\nDEGREE:{n_deg}:BASELINE_REDUCED_ONLY SET UP:START...")
                
                df_bo = Baseline_Reduced()
                df_bo = df_bo.drop(['uuid'],axis=1)
                df_simple = df_bo
                X_train,X_test,X,y,y_train,y_test,numeric_features,\
                categorical_features = gen_Train_Test_Split(df_simple)
                X_train,X_test = PCA_Industry(X_train,X_test)
                X_train,X_test = PCA_Country(X_train,X_test)
                
                #Visualize_Country_Ind_PCA(X,y)
                print("Final train dataset shape",X_train.shape)
                print("\nFinal test dataset shape",X_test.shape)
                #print('\nTrain Dataframe Columns:\n\n{}'.format(X_train.columns.to_list()))
                #print('\nTest Dataframe Columns:\n\n{}'.format(X_test.columns.to_list()))
                col_graph = 'None'
                results = Run_Classifier(X_train,X_test,y_train,y_test,numeric_features,categorical_features,setup_Type,col_graph)
                out_list.append(results)
                print(f"\nDEGREE:{n_deg}:BASELINE_REDUCED_ONLY SET UP:END")

        out_dict['result'] = out_list
        final_out.append(out_dict)
        print(f"\nDEGREE:{n_deg}:ITERATION:{iteration+1} END")    
        Write_Output(final_out)
    
                  
if __name__ == "__main__":
    # execute only if run as a script
    main()


DEGREE:2:ITERATION:1 BEGIN...

DEGREE:2:BASELINE_ONLY SET UP:START...
Original DF shape (1131326, 3)
Original Model_DF_D2 shape (1131326, 3)
Original DF_GR shape after merge (10343, 41)
Mem. usage decreased to  1.43 Mb (56.8% reduction)
(3874, 39)
Mem. usage decreased to  0.89 Mb (0.0% reduction)
Numeric features: ['pr_0', 'pr_1', 'pr_2', 'pr_3', 'kc_0', 'kc_1', 'kc_2', 'kc_3', 'in_deg_0', 'out_deg_0', 'in_deg_1', 'out_deg_1', 'tri_0', 'tri_1', 'spath_top_1_0', 'spath_top_1_1', 'spath_top_1_2', 'spath_top_1_3', 'spath_top_1_4', 'spath_top_min_1', 'spath_top_3_0', 'spath_top_3_1', 'spath_top_3_2', 'spath_top_3_3', 'spath_top_3_4', 'spath_top_min_3', 'w_spath_top_1_0', 'w_spath_top_1_1', 'w_spath_top_1_2', 'w_spath_top_1_3', 'w_spath_top_1_4', 'w_spath_top_min_1', 'w_spath_top_3_0', 'w_spath_top_3_1', 'w_spath_top_3_2', 'w_spath_top_3_3', 'w_spath_top_3_4', 'w_spath_top_min_3']
Categorical features: []
Training data shape: (6198, 38)
Train label shape: (6198,)
Test data shape: (1550, 38

Merged shape after baseline and graph (10527, 264)
df_bo shape (1131326, 265)
df_temp shape (10492, 3)
df_simple shape (10527, 264)
(3908, 264)
Mem. usage decreased to  2.38 Mb (8.1% reduction)
Numeric features: ['rank', 'employee_count_ord', 'total_funding_usd', 'ind_1', 'ind_2', 'ind_3', 'ind_4', 'ind_5', 'ind_6', 'ind_7', 'ind_8', 'ind_9', 'ind_10', 'ind_11', 'ind_12', 'ind_13', 'ind_14', 'ind_15', 'ind_16', 'ind_17', 'ind_18', 'ind_19', 'ind_20', 'ind_21', 'ind_22', 'ind_23', 'ind_24', 'ind_25', 'ind_26', 'ind_27', 'ind_28', 'ind_29', 'ind_30', 'ind_31', 'ind_32', 'ind_33', 'ind_34', 'ind_35', 'ind_36', 'ind_37', 'ind_38', 'ind_39', 'ind_40', 'ind_41', 'ind_42', 'ind_43', 'ind_44', 'ind_45', 'ind_46', 'age', 'country_0', 'country_ABW', 'country_AFG', 'country_AGO', 'country_AIA', 'country_ALA', 'country_ALB', 'country_AND', 'country_ARE', 'country_ARG', 'country_ARM', 'country_ASM', 'country_ATG', 'country_AUS', 'country_AUT', 'country_AZE', 'country_BAH', 'country_BDI', 'country_B

Merged shape after baseline and graph (10527, 265)
df_bo shape (1131326, 265)
df_temp shape (10492, 4)
df_simple shape (10527, 265)
(3908, 265)
Mem. usage decreased to  2.41 Mb (8.0% reduction)
Numeric features: ['spath_top_1_1', 'rank', 'employee_count_ord', 'total_funding_usd', 'ind_1', 'ind_2', 'ind_3', 'ind_4', 'ind_5', 'ind_6', 'ind_7', 'ind_8', 'ind_9', 'ind_10', 'ind_11', 'ind_12', 'ind_13', 'ind_14', 'ind_15', 'ind_16', 'ind_17', 'ind_18', 'ind_19', 'ind_20', 'ind_21', 'ind_22', 'ind_23', 'ind_24', 'ind_25', 'ind_26', 'ind_27', 'ind_28', 'ind_29', 'ind_30', 'ind_31', 'ind_32', 'ind_33', 'ind_34', 'ind_35', 'ind_36', 'ind_37', 'ind_38', 'ind_39', 'ind_40', 'ind_41', 'ind_42', 'ind_43', 'ind_44', 'ind_45', 'ind_46', 'age', 'country_0', 'country_ABW', 'country_AFG', 'country_AGO', 'country_AIA', 'country_ALA', 'country_ALB', 'country_AND', 'country_ARE', 'country_ARG', 'country_ARM', 'country_ASM', 'country_ATG', 'country_AUS', 'country_AUT', 'country_AZE', 'country_BAH', 'country

Merged shape after baseline and graph (10527, 265)
df_bo shape (1131326, 265)
df_temp shape (10492, 4)
df_simple shape (10527, 265)
(3908, 265)
Mem. usage decreased to  2.41 Mb (8.0% reduction)
Numeric features: ['w_spath_top_1_2', 'rank', 'employee_count_ord', 'total_funding_usd', 'ind_1', 'ind_2', 'ind_3', 'ind_4', 'ind_5', 'ind_6', 'ind_7', 'ind_8', 'ind_9', 'ind_10', 'ind_11', 'ind_12', 'ind_13', 'ind_14', 'ind_15', 'ind_16', 'ind_17', 'ind_18', 'ind_19', 'ind_20', 'ind_21', 'ind_22', 'ind_23', 'ind_24', 'ind_25', 'ind_26', 'ind_27', 'ind_28', 'ind_29', 'ind_30', 'ind_31', 'ind_32', 'ind_33', 'ind_34', 'ind_35', 'ind_36', 'ind_37', 'ind_38', 'ind_39', 'ind_40', 'ind_41', 'ind_42', 'ind_43', 'ind_44', 'ind_45', 'ind_46', 'age', 'country_0', 'country_ABW', 'country_AFG', 'country_AGO', 'country_AIA', 'country_ALA', 'country_ALB', 'country_AND', 'country_ARE', 'country_ARG', 'country_ARM', 'country_ASM', 'country_ATG', 'country_AUS', 'country_AUT', 'country_AZE', 'country_BAH', 'count

Merged shape after baseline and graph (10527, 265)
df_bo shape (1131326, 265)
df_temp shape (10492, 4)
df_simple shape (10527, 265)
(3908, 265)
Mem. usage decreased to  2.41 Mb (8.0% reduction)
Numeric features: ['w_spath_top_1_3', 'rank', 'employee_count_ord', 'total_funding_usd', 'ind_1', 'ind_2', 'ind_3', 'ind_4', 'ind_5', 'ind_6', 'ind_7', 'ind_8', 'ind_9', 'ind_10', 'ind_11', 'ind_12', 'ind_13', 'ind_14', 'ind_15', 'ind_16', 'ind_17', 'ind_18', 'ind_19', 'ind_20', 'ind_21', 'ind_22', 'ind_23', 'ind_24', 'ind_25', 'ind_26', 'ind_27', 'ind_28', 'ind_29', 'ind_30', 'ind_31', 'ind_32', 'ind_33', 'ind_34', 'ind_35', 'ind_36', 'ind_37', 'ind_38', 'ind_39', 'ind_40', 'ind_41', 'ind_42', 'ind_43', 'ind_44', 'ind_45', 'ind_46', 'age', 'country_0', 'country_ABW', 'country_AFG', 'country_AGO', 'country_AIA', 'country_ALA', 'country_ALB', 'country_AND', 'country_ARE', 'country_ARG', 'country_ARM', 'country_ASM', 'country_ATG', 'country_AUS', 'country_AUT', 'country_AZE', 'country_BAH', 'count

...

Best parameter (CV score=0.770): {'classifier__random_state': None, 'classifier__C': 10.0}
Best score: 0.7698

KNN with OneHotEncoder and StandardScaler()
Score: 0.7639

BNB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.692): {'classifier__alpha': 0.0001}
Best score: 0.7036

GNB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.737): {'classifier__var_smoothing': 0.0001}
Best score: 0.7252

DCT with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.778): {'classifier__random_state': None, 'classifier__min_samples_leaf': 20, 'classifier__max_depth': 10}
Best score: 0.7794

XGB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.466): {'classifier__random_state': None}
Best score: 0.8266

RMF with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.822): {'classifier__random_state': None}
Best score: 0.8381

SVM with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.785): {'classifier__random_state': N

Best parameter (CV score=0.732): {'classifier__random_state': None, 'classifier__C': 10.0}
Best score: 0.7178

KNN with OneHotEncoder and StandardScaler()
Score: 0.7177

BNB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.635): {'classifier__alpha': 0.0001}
Best score: 0.6531

GNB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.672): {'classifier__var_smoothing': 0.0001}
Best score: 0.6581

DCT with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.742): {'classifier__random_state': None, 'classifier__min_samples_leaf': 50, 'classifier__max_depth': 9}
Best score: 0.7363

XGB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.403): {'classifier__random_state': None}
Best score: 0.7807

RMF with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.806): {'classifier__random_state': None}
Best score: 0.8030

SVM with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.741): {'classifier__random_state': No

Best parameter (CV score=0.725): {'classifier__random_state': None, 'classifier__C': 0.1}
Best score: 0.7456

KNN with OneHotEncoder and StandardScaler()
Score: 0.7193

BNB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.649): {'classifier__alpha': 0.0001}
Best score: 0.6939

GNB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.665): {'classifier__var_smoothing': 0.0001}
Best score: 0.6709

DCT with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.725): {'classifier__random_state': None, 'classifier__min_samples_leaf': 100, 'classifier__max_depth': 16}
Best score: 0.7286

XGB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.350): {'classifier__random_state': None}
Best score: 0.7886

RMF with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.786): {'classifier__random_state': None}
Best score: 0.8209

SVM with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.736): {'classifier__random_state': N

Best parameter (CV score=0.738): {'classifier__random_state': None, 'classifier__C': 1.0}
Best score: 0.7379

KNN with OneHotEncoder and StandardScaler()
Score: 0.7161

BNB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.643): {'classifier__alpha': 0.0001}
Best score: 0.6754

GNB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.681): {'classifier__var_smoothing': 0.0001}
Best score: 0.6884

DCT with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.759): {'classifier__random_state': None, 'classifier__min_samples_leaf': 50, 'classifier__max_depth': 14}
Best score: 0.7800

XGB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.445): {'classifier__random_state': None}
Best score: 0.8347

RMF with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.819): {'classifier__random_state': None}
Best score: 0.8421

SVM with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.742): {'classifier__random_state': No

Best parameter (CV score=0.730): {'classifier__random_state': None, 'classifier__C': 1.0}
Best score: 0.7184

KNN with OneHotEncoder and StandardScaler()
Score: 0.6970

BNB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.650): {'classifier__alpha': 10.0}
Best score: 0.6480

GNB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.672): {'classifier__var_smoothing': 0.001}
Best score: 0.6656

DCT with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.742): {'classifier__random_state': None, 'classifier__min_samples_leaf': 20, 'classifier__max_depth': 14}
Best score: 0.7462

XGB with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.401): {'classifier__random_state': None}
Best score: 0.8043

RMF with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.804): {'classifier__random_state': None}
Best score: 0.8171

SVM with OneHotEncoder and StandardScaler()
Best parameter (CV score=0.740): {'classifier__random_state': None}